In [1]:
import geopandas as gpd
import pandas as pd
import polars as pl

from great_tables import GT, _data_color, loc, md, nanoplot_options, style

from update_vars import BUS_SERVICE_GCS

In [2]:
def category_wrangling(
    df: pd.DataFrame, 
    col: str = "category", 
    sort_key: list = ["on_shn", "parallel", "other", "shn_subtotal", "total"]
) -> pd.DataFrame:
    """
    Custom sort order for categorical variable
    https://stackoverflow.com/questions/23482668/sorting-by-a-custom-list-in-pandas
    """
    category_values = {
        "on_shn": "On SHN", 
        "parallel": "Intersects SHN",
        "other": "Other",
        "shn_subtotal": "On or Intersects SHN",
        "total": "Total"
    }
    
    df = df.sort_values(
        col, key=lambda c: c.map(lambda e: sort_key.index(e))
    ) 
    
    df = df.assign(
        category = df.category.map(category_values)
    )
    
    return df

def get_hex(color_name: str) -> str:
    """
    Since some of the color names don't pull the hex code, 
    we'll grab it here.
    https://github.com/posit-dev/great-tables/blob/main/great_tables/_data_color/constants.py
    """
    return _data_color.constants.COLOR_NAME_TO_HEX[color_name]

In [3]:
current_quarter = "2024-Q2"

operator_df = pd.read_parquet(
    f"{BUS_SERVICE_GCS}"
    "quarterly_metrics/operator_time_series.parquet",
    filters = [[("year_quarter", "==", current_quarter)]]
).pipe(category_wrangling)

district_df = pd.read_parquet(
    f"{BUS_SERVICE_GCS}"
    "quarterly_metrics/district_time_series.parquet",
    filters = [[("year_quarter", "==", current_quarter)]]
).pipe(category_wrangling)

statewide_df = pd.read_parquet(
    f"{BUS_SERVICE_GCS}"
    "quarterly_metrics/statewide_time_series.parquet",
    filters = [[("year_quarter", "==", current_quarter)]]
).pipe(category_wrangling)

In [4]:
def shared_nano_options(
    point_stroke_color: str = "black",
    line_stroke_color: str = "black",
    point_fill_color: str = "white",
    area_fill_color: str = "white"
):
    nano_options = nanoplot_options(
        data_point_radius=6,
        data_point_stroke_color=get_hex(point_stroke_color),
        data_point_fill_color=get_hex(point_fill_color),
        data_point_stroke_width=4,
        data_line_type="curved",
        data_line_stroke_color=get_hex(line_stroke_color),
        data_line_stroke_width=8,
        data_area_fill_color=get_hex(area_fill_color),
        #vertical_guide_stroke_color=None,
        show_y_axis_guide=True,
        #show_vertical_guides=False,
        interactive_data_values = True,
        #reference_line_color=get_hex("salmon1"),
        show_reference_line=False
    )
    
    return nano_options


def table_settings(table):
    table2 = (
        table.tab_options(
            container_width = "100%",
            table_background_color="white",
            table_body_hlines_style="none",
            table_body_vlines_style="none",
            heading_background_color="white",
            column_labels_background_color="white",
            row_group_background_color="white",
            stub_background_color="white",
            source_notes_background_color="white",
            table_font_size="14px",
            heading_align="center"
        )
    )
    
    return table2

In [5]:
def plot_table(df: pd.DataFrame): 
    
    service_col = "service_hours_per_route"
    speed_col = "speed_mph"
    
    MIN_SPEED, MAX_SPEED = df[speed_col].min(), df[speed_col].max()
    MIN_SERVICE, MAX_SERVICE = df[service_col].min(), df[service_col].max()
    
    exclude_me = [
        "year_quarter", "service_hours", "n_routes", 
        "n_dates", "n_vp_routes", 
    ] + [i for i in df.columns if "prior_" in i or 
        "pct_change" in i]
    
    table = (
        GT(pl.from_pandas(df))
        .fmt_nanoplot(
            columns=f"{speed_col}_ts",
            plot_type="line",
            expand_y=[round(MIN_SPEED, 0), round(MAX_SPEED, 0)],
            options=shared_nano_options(
                point_stroke_color = "black",
                line_stroke_color = "green",
                point_fill_color = "white",
                area_fill_color = "seagreen2")
        ).fmt_nanoplot(
            columns=f"{service_col}_ts",
            plot_type="line",
            expand_y=[round(MIN_SERVICE, 0), round(MAX_SERVICE, 0)],
            options=shared_nano_options(
                point_stroke_color = "black", 
                line_stroke_color = "steelblue1",
                point_fill_color = "white",
                area_fill_color = "lightskyblue2", 
            )
        ).fmt_number(
            columns = [
                "daily_service_hours", service_col, speed_col,
                f"change_{service_col}", f"change_{speed_col}"
            ], decimals=1
        ).fmt_integer(
            columns = ["daily_routes", "daily_vp_routes"]
         ).cols_label(
            category = "Category",
            daily_service_hours = "Daily Service Hours",
            service_hours_per_route = "Service Hours per Route",
            speed_mph = "Average Speed",
            daily_routes = "# Routes",
            daily_vp_routes = "# Routes",
            service_hours_per_route_ts = "Time-series",
            speed_mph_ts = "Time-series",
            change_service_hours_per_route = "Change from Prior",
            change_speed_mph = "Change from Prior",
            pct_change_service_hours_per_route = "% Change",
            pct_change_speed_mph = "% Change"
         ).tab_header(
             title = "Service Hours and Speed",
             subtitle = f"{current_quarter}"
         ).tab_spanner(
            label="Service", 
            columns=["daily_service_hours", 
                     service_col, "daily_routes", 
                     f"change_{service_col}", f"pct_change_{service_col}",
                     f"{service_col}_ts", 
                    ]
        ).tab_spanner(
            label="Speed (mph)",
            columns = [speed_col, 
                       "daily_vp_routes",
                       f"change_{speed_col}", f"pct_change_{speed_col}",
                       f"{speed_col}_ts"]
        ).cols_hide(
            exclude_me
        ).sub_missing(
            columns = [speed_col, f"{speed_col}_ts", "daily_vp_routes", f"change_{speed_col}"],
            missing_text = ""
        )
        # start styling the subtotals / totals
        .tab_style(
            style=style.text(weight="bold"),
            locations=loc.body(rows=pl.col("category") == "Total")
        ).tab_style(
            style=style.text(
                weight="normal", style="italic", color=get_hex("gray20")),
            locations=loc.body(
                rows=pl.col("category") == "On or Intersects SHN"),
        ).cols_align(align="center")
         .cols_align(align="left", columns="category")
        # flag whether change from prior is positive of negative
        # https://posit-dev.github.io/great-tables/get-started/basic-styling.html
        #.tab_style(
        #    style=style.fill(color="#d8ffd8"), # super pale green
        #    locations=loc.body(
        #        columns=f"change_{speed_col}",
        #        rows=pl.col(f"change_{speed_col}") > 0
        #    )
        #)
        .data_color(
            palette = [get_hex("indianred1"), get_hex("whitesmoke"), get_hex("mediumspringgreen")],
            #domain = [-2, 2], 
            na_color="white",
            columns = f"change_{service_col}"
        ).data_color(
            palette = [get_hex("indianred1"), get_hex("whitesmoke"), get_hex("mediumspringgreen")],
            #domain = [-2, 2], 
            na_color="white",
            columns = f"change_{speed_col}"
        )
    )
    
    table = table_settings(table)
    
    return table

## Statewide Metrics

In [6]:
def statewide_table_specs(table): 
    table2 = (table
      # add dotted line separating subtotals from categories
        # https://posit-dev.github.io/great-tables/reference/GT.html#great_tables.GT.tab_style
        .tab_style(
            style=style.borders(sides=["top", "bottom"], weight='2px', color="black"),
            locations=loc.body(rows=[3, 4])
        )
    )
    
    return table2
    
table = plot_table(statewide_df)
statewide_table_specs(table)

GT(_tbl_data=shape: (5, 19)
┌───────────┬───────────┬───────────┬──────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ category  ┆ year_quar ┆ service_h ┆ n_routes ┆ … ┆ change_sp ┆ pct_chang ┆ service_h ┆ speed_mph │
│ ---       ┆ ter       ┆ ours      ┆ ---      ┆   ┆ eed_mph   ┆ e_speed_m ┆ ours_per_ ┆ _ts       │
│ str       ┆ ---       ┆ ---       ┆ i64      ┆   ┆ ---       ┆ ph        ┆ route_ts  ┆ ---       │
│           ┆ str       ┆ f64       ┆          ┆   ┆ f64       ┆ ---       ┆ ---       ┆ list[f64] │
│           ┆           ┆           ┆          ┆   ┆           ┆ f64       ┆ list[f64] ┆           │
╞═══════════╪═══════════╪═══════════╪══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ On SHN    ┆ 2024-Q2   ┆ 32998.4   ┆ 1457     ┆ … ┆ 0.43      ┆ 1.9       ┆ [22.57,   ┆ [22.32,   │
│           ┆           ┆           ┆          ┆   ┆           ┆           ┆ 22.55, …  ┆ 22.54, …  │
│           ┆           ┆           ┆          ┆   ┆           ┆           ┆ 22.65]    ┆ 22.61]    │
│ Intersect ┆ 2024-Q2   ┆ 123381.99 ┆ 3384     ┆ … ┆ 0.65      ┆ 4.6       ┆ [37.54,   ┆ [14.11,   │
│ s SHN     ┆           ┆           ┆          ┆   ┆           ┆           ┆ 37.32, …  ┆ 14.11, …  │
│           ┆           ┆           ┆          ┆   ┆           ┆           ┆ 36.46]    ┆ 14.01]    │
│ Other     ┆ 2024-Q2   ┆ 60180.48  ┆ 1293     ┆ … ┆ 0.53      ┆ 3.6       ┆ [46.22,   ┆ [14.65,   │
│           ┆           ┆           ┆          ┆   ┆           ┆           ┆ 46.11, …  ┆ 14.64, …  │
│           ┆           ┆           ┆          ┆   ┆           ┆           ┆ 46.54]    ┆ 14.68]    │
│ On or Int ┆ 2024-Q2   ┆ 156380.39 ┆ 4841     ┆ … ┆ 0.6       ┆ 3.7       ┆ [33.24,   ┆ [15.98,   │
│ ersects   ┆           ┆           ┆          ┆   ┆           ┆           ┆ 32.97, …  ┆ 16.19, …  │
│ SHN       ┆           ┆           ┆          ┆   ┆           ┆           ┆ 32.3]     ┆ 16.21]    │
│ Total     ┆ 2024-Q2   ┆ 216560.87 ┆ 6134     ┆ … ┆ 0.58      ┆ 3.7       ┆ [35.93,   ┆ [15.69,   │
│           ┆           ┆           ┆          ┆   ┆           ┆           ┆ 35.75, …  ┆ 15.85, …  │
│           ┆           ┆           ┆          ┆   ┆           ┆           ┆ 35.3]     ┆ 15.87]    │
└───────────┴───────────┴───────────┴──────────┴───┴───────────┴───────────┴───────────┴───────────┘, _body=<great_tables._gt_data.Body object at 0x79795182bb20>, _boxhead=Boxhead([ColInfo(var='category', type=<ColInfoTypeEnum.default: 1>, column_label='Category', column_align='left', column_width=None), ColInfo(var='year_quarter', type=<ColInfoTypeEnum.hidden: 4>, column_label='year_quarter', column_align='center', column_width=None), ColInfo(var='service_hours', type=<ColInfoTypeEnum.hidden: 4>, column_label='service_hours', column_align='center', column_width=None), ColInfo(var='n_routes', type=<ColInfoTypeEnum.hidden: 4>, column_label='n_routes', column_align='center', column_width=None), ColInfo(var='n_dates', type=<ColInfoTypeEnum.hidden: 4>, column_label='n_dates', column_align='center', column_width=None), ColInfo(var='daily_service_hours', type=<ColInfoTypeEnum.default: 1>, column_label='Daily Service Hours', column_align='center', column_width=None), ColInfo(var='service_hours_per_route', type=<ColInfoTypeEnum.default: 1>, column_label='Service Hours per Route', column_align='center', column_width=None), ColInfo(var='daily_routes', type=<ColInfoTypeEnum.default: 1>, column_label='# Routes', column_align='center', column_width=None), ColInfo(var='change_service_hours_per_route', type=<ColInfoTypeEnum.default: 1>, column_label='Change from Prior', column_align='center', column_width=None), ColInfo(var='pct_change_service_hours_per_route', type=<ColInfoTypeEnum.hidden: 4>, column_label='% Change', column_align='center', column_width=None), ColInfo(var='service_hours_per_route_ts', type=<ColInfoTypeEnum.default: 1>, column_label='Time-series', column_align='center', column_width=None), ColInfo(var='speed_mph', type

## District Breakdown

In [7]:
def district_table_specs(table, one_district, one_quarter):
    service_col = "service_hours_per_route"
    speed_col = "speed_mph"
    
    table2 = (table
              .cols_hide("caltrans_district")
              .tab_header(
                 title = f"District {one_district}",
                 subtitle = f"Service Hours and Speed  {one_quarter}")
             ).data_color(
            palette = [get_hex("indianred1"), get_hex("whitesmoke"), get_hex("mediumspringgreen")],
            #domain = [-10, 10], 
            na_color="white",
            columns = f"change_{service_col}"
        ).data_color(
            palette = [get_hex("indianred1"), get_hex("whitesmoke"), get_hex("mediumspringgreen")],
            #domain = [-4, 4], 
            na_color="white",
            columns = f"change_{speed_col}"
        )
    
    return table2
    

for i in sorted(district_df.caltrans_district.unique()):
    table = plot_table(
        district_df[district_df.caltrans_district==i])
    
    table = district_table_specs(table, i, current_quarter)

    display(table)

GT(_tbl_data=shape: (5, 20)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ caltrans_ ┆ category  ┆ year_quar ┆ service_h ┆ … ┆ change_sp ┆ pct_chang ┆ service_h ┆ speed_mp │
│ district  ┆ ---       ┆ ter       ┆ ours      ┆   ┆ eed_mph   ┆ e_speed_m ┆ ours_per_ ┆ h_ts     │
│ ---       ┆ str       ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ph        ┆ route_ts  ┆ ---      │
│ str       ┆           ┆ str       ┆ f64       ┆   ┆ f64       ┆ ---       ┆ ---       ┆ list[f64 │
│           ┆           ┆           ┆           ┆   ┆           ┆ f64       ┆ list[f64] ┆ ]        │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 01 -      ┆ On SHN    ┆ 2024-Q2   ┆ 369.25    ┆ … ┆ 1.74      ┆ 5.6       ┆ [9.71,    ┆ [31.21,  │
│ Eureka    ┆           ┆           ┆           ┆   ┆           ┆           ┆ 9.59, …   ┆ 30.58, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 10.26]    ┆ 31.18]   │
│ 01 -      ┆ Intersect ┆ 2024-Q2   ┆ 382.51    ┆ … ┆ 0.98      ┆ 6.1       ┆ [9.07,    ┆ [20.1,   │
│ Eureka    ┆ s SHN     ┆           ┆           ┆   ┆           ┆           ┆ 9.08, …   ┆ 16.29, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 9.81]     ┆ 15.95]   │
│ 01 -      ┆ Other     ┆ 2024-Q2   ┆ 56.42     ┆ … ┆ null      ┆ null      ┆ [15.86,   ┆ [null,   │
│ Eureka    ┆           ┆           ┆           ┆   ┆           ┆           ┆ 15.86, …  ┆ null, …  │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 18.81]    ┆ null]    │
│ 01 -      ┆ On or Int ┆ 2024-Q2   ┆ 751.76    ┆ … ┆ 1.64      ┆ 7.0       ┆ [9.38,    ┆ [25.65,  │
│ Eureka    ┆ ersects   ┆           ┆           ┆   ┆           ┆           ┆ 9.33, …   ┆ 23.79, … │
│           ┆ SHN       ┆           ┆           ┆   ┆           ┆           ┆ 10.02]    ┆ 23.35]   │
│ 01 -      ┆ Total     ┆ 2024-Q2   ┆ 808.18    ┆ … ┆ 1.64      ┆ 7.0       ┆ [9.89,    ┆ [25.65,  │
│ Eureka    ┆           ┆           ┆           ┆   ┆           ┆           ┆ 9.85, …   ┆ 23.79, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 10.36]    ┆ 23.35]   │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘, _body=<great_tables._gt_data.Body object at 0x7979514aa700>, _boxhead=Boxhead([ColInfo(var='caltrans_district', type=<ColInfoTypeEnum.hidden: 4>, column_label='caltrans_district', column_align='center', column_width=None), ColInfo(var='category', type=<ColInfoTypeEnum.default: 1>, column_label='Category', column_align='left', column_width=None), ColInfo(var='year_quarter', type=<ColInfoTypeEnum.hidden: 4>, column_label='year_quarter', column_align='center', column_width=None), ColInfo(var='service_hours', type=<ColInfoTypeEnum.hidden: 4>, column_label='service_hours', column_align='center', column_width=None), ColInfo(var='n_routes', type=<ColInfoTypeEnum.hidden: 4>, column_label='n_routes', column_align='center', column_width=None), ColInfo(var='n_dates', type=<ColInfoTypeEnum.hidden: 4>, column_label='n_dates', column_align='center', column_width=None), ColInfo(var='daily_service_hours', type=<ColInfoTypeEnum.default: 1>, column_label='Daily Service Hours', column_align='center', column_width=None), ColInfo(var='service_hours_per_route', type=<ColInfoTypeEnum.default: 1>, column_label='Service Hours per Route', column_align='center', column_width=None), ColInfo(var='daily_routes', type=<ColInfoTypeEnum.default: 1>, column_label='# Routes', column_align='center', column_width=None), ColInfo(var='change_service_hours_per_route', type=<ColInfoTypeEnum.default: 1>, column_label='Change from Prior', column_align='center', column_width=None), ColInfo(var='pct_change_service_hours_per_route', type=<ColInfoTypeEnum.hidden: 4>, column_label='% Change', column_align='center', column_width=None), ColInfo(var='service_hours_per_ro

GT(_tbl_data=shape: (4, 20)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ caltrans_ ┆ category  ┆ year_quar ┆ service_h ┆ … ┆ change_sp ┆ pct_chang ┆ service_h ┆ speed_mp │
│ district  ┆ ---       ┆ ter       ┆ ours      ┆   ┆ eed_mph   ┆ e_speed_m ┆ ours_per_ ┆ h_ts     │
│ ---       ┆ str       ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ph        ┆ route_ts  ┆ ---      │
│ str       ┆           ┆ str       ┆ f64       ┆   ┆ f64       ┆ ---       ┆ ---       ┆ list[f64 │
│           ┆           ┆           ┆           ┆   ┆           ┆ f64       ┆ list[f64] ┆ ]        │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 02 -      ┆ On SHN    ┆ 2024-Q2   ┆ 720.63    ┆ … ┆ 0.63      ┆ 2.8       ┆ [7.73,    ┆ [20.13,  │
│ Redding   ┆           ┆           ┆           ┆   ┆           ┆           ┆ 7.81, …   ┆ 20.81, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 8.01]     ┆ 22.43]   │
│ 02 -      ┆ Intersect ┆ 2024-Q2   ┆ 327.95    ┆ … ┆ 0.82      ┆ 4.6       ┆ [9.81,    ┆ [18.0,   │
│ Redding   ┆ s SHN     ┆           ┆           ┆   ┆           ┆           ┆ 9.78, …   ┆ 17.8, …  │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 9.65]     ┆ 17.71]   │
│ 02 -      ┆ On or Int ┆ 2024-Q2   ┆ 1048.58   ┆ … ┆ 0.84      ┆ 4.2       ┆ [8.4,     ┆ [18.89,  │
│ Redding   ┆ ersects   ┆           ┆           ┆   ┆           ┆           ┆ 8.44, …   ┆ 19.31, … │
│           ┆ SHN       ┆           ┆           ┆   ┆           ┆           ┆ 8.46]     ┆ 20.18]   │
│ 02 -      ┆ Total     ┆ 2024-Q2   ┆ 1048.58   ┆ … ┆ 0.84      ┆ 4.2       ┆ [8.28,    ┆ [18.89,  │
│ Redding   ┆           ┆           ┆           ┆   ┆           ┆           ┆ 8.31, …   ┆ 19.31, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 8.46]     ┆ 20.18]   │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘, _body=<great_tables._gt_data.Body object at 0x7979518223a0>, _boxhead=Boxhead([ColInfo(var='caltrans_district', type=<ColInfoTypeEnum.hidden: 4>, column_label='caltrans_district', column_align='center', column_width=None), ColInfo(var='category', type=<ColInfoTypeEnum.default: 1>, column_label='Category', column_align='left', column_width=None), ColInfo(var='year_quarter', type=<ColInfoTypeEnum.hidden: 4>, column_label='year_quarter', column_align='center', column_width=None), ColInfo(var='service_hours', type=<ColInfoTypeEnum.hidden: 4>, column_label='service_hours', column_align='center', column_width=None), ColInfo(var='n_routes', type=<ColInfoTypeEnum.hidden: 4>, column_label='n_routes', column_align='center', column_width=None), ColInfo(var='n_dates', type=<ColInfoTypeEnum.hidden: 4>, column_label='n_dates', column_align='center', column_width=None), ColInfo(var='daily_service_hours', type=<ColInfoTypeEnum.default: 1>, column_label='Daily Service Hours', column_align='center', column_width=None), ColInfo(var='service_hours_per_route', type=<ColInfoTypeEnum.default: 1>, column_label='Service Hours per Route', column_align='center', column_width=None), ColInfo(var='daily_routes', type=<ColInfoTypeEnum.default: 1>, column_label='# Routes', column_align='center', column_width=None), ColInfo(var='change_service_hours_per_route', type=<ColInfoTypeEnum.default: 1>, column_label='Change from Prior', column_align='center', column_width=None), ColInfo(var='pct_change_service_hours_per_route', type=<ColInfoTypeEnum.hidden: 4>, column_label='% Change', column_align='center', column_width=None), ColInfo(var='service_hours_per_route_ts', type=<ColInfoTypeEnum.default: 1>, column_label='Time-series', column_align='center', column_width=None), ColInfo(var='speed_mph', type=<ColInfoTypeEnum.default: 1>, column_label='Average Speed', column_align='center', column_width=None), ColInfo(var='daily_vp_routes', type=<ColInfoTypeEnum.de

GT(_tbl_data=shape: (5, 20)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ caltrans_ ┆ category  ┆ year_quar ┆ service_h ┆ … ┆ change_sp ┆ pct_chang ┆ service_h ┆ speed_mp │
│ district  ┆ ---       ┆ ter       ┆ ours      ┆   ┆ eed_mph   ┆ e_speed_m ┆ ours_per_ ┆ h_ts     │
│ ---       ┆ str       ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ph        ┆ route_ts  ┆ ---      │
│ str       ┆           ┆ str       ┆ f64       ┆   ┆ f64       ┆ ---       ┆ ---       ┆ list[f64 │
│           ┆           ┆           ┆           ┆   ┆           ┆ f64       ┆ list[f64] ┆ ]        │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 03 - Mary ┆ On SHN    ┆ 2024-Q2   ┆ 1408.74   ┆ … ┆ 0.39      ┆ 1.6       ┆ [7.64,    ┆ [22.65,  │
│ sville    ┆           ┆           ┆           ┆   ┆           ┆           ┆ 8.04, …   ┆ 22.98, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 7.19]     ┆ 23.72]   │
│ 03 - Mary ┆ Intersect ┆ 2024-Q2   ┆ 3075.63   ┆ … ┆ -0.15     ┆ -1.1      ┆ [12.77,   ┆ [14.14,  │
│ sville    ┆ s SHN     ┆           ┆           ┆   ┆           ┆           ┆ 16.38, …  ┆ 14.33, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 15.15]    ┆ 13.86]   │
│ 03 - Mary ┆ Other     ┆ 2024-Q2   ┆ 1321.84   ┆ … ┆ 0.69      ┆ 3.9       ┆ [10.81,   ┆ [18.81,  │
│ sville    ┆           ┆           ┆           ┆   ┆           ┆           ┆ 22.68, …  ┆ 17.34, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 17.39]    ┆ 17.49]   │
│ 03 - Mary ┆ On or Int ┆ 2024-Q2   ┆ 4484.37   ┆ … ┆ 0.26      ┆ 1.5       ┆ [10.09,   ┆ [17.6,   │
│ sville    ┆ ersects   ┆           ┆           ┆   ┆           ┆           ┆ 12.61, …  ┆ 17.99, … │
│           ┆ SHN       ┆           ┆           ┆   ┆           ┆           ┆ 11.24]    ┆ 17.86]   │
│ 03 - Mary ┆ Total     ┆ 2024-Q2   ┆ 5806.21   ┆ … ┆ 0.35      ┆ 2.0       ┆ [10.18,   ┆ [17.91,  │
│ sville    ┆           ┆           ┆           ┆   ┆           ┆           ┆ 14.3, …   ┆ 17.82, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 12.22]    ┆ 17.78]   │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘, _body=<great_tables._gt_data.Body object at 0x7979517dda00>, _boxhead=Boxhead([ColInfo(var='caltrans_district', type=<ColInfoTypeEnum.hidden: 4>, column_label='caltrans_district', column_align='center', column_width=None), ColInfo(var='category', type=<ColInfoTypeEnum.default: 1>, column_label='Category', column_align='left', column_width=None), ColInfo(var='year_quarter', type=<ColInfoTypeEnum.hidden: 4>, column_label='year_quarter', column_align='center', column_width=None), ColInfo(var='service_hours', type=<ColInfoTypeEnum.hidden: 4>, column_label='service_hours', column_align='center', column_width=None), ColInfo(var='n_routes', type=<ColInfoTypeEnum.hidden: 4>, column_label='n_routes', column_align='center', column_width=None), ColInfo(var='n_dates', type=<ColInfoTypeEnum.hidden: 4>, column_label='n_dates', column_align='center', column_width=None), ColInfo(var='daily_service_hours', type=<ColInfoTypeEnum.default: 1>, column_label='Daily Service Hours', column_align='center', column_width=None), ColInfo(var='service_hours_per_route', type=<ColInfoTypeEnum.default: 1>, column_label='Service Hours per Route', column_align='center', column_width=None), ColInfo(var='daily_routes', type=<ColInfoTypeEnum.default: 1>, column_label='# Routes', column_align='center', column_width=None), ColInfo(var='change_service_hours_per_route', type=<ColInfoTypeEnum.default: 1>, column_label='Change from Prior', column_align='center', column_width=None), ColInfo(var='pct_change_service_hours_per_route', type=<ColInfoTypeEnum.hidden: 4>, column_label='% Change', column_align='center', column_width=None), ColInfo(var='service_hours_per_ro

GT(_tbl_data=shape: (5, 20)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ caltrans_ ┆ category  ┆ year_quar ┆ service_h ┆ … ┆ change_sp ┆ pct_chang ┆ service_h ┆ speed_mp │
│ district  ┆ ---       ┆ ter       ┆ ours      ┆   ┆ eed_mph   ┆ e_speed_m ┆ ours_per_ ┆ h_ts     │
│ ---       ┆ str       ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ph        ┆ route_ts  ┆ ---      │
│ str       ┆           ┆ str       ┆ f64       ┆   ┆ f64       ┆ ---       ┆ ---       ┆ list[f64 │
│           ┆           ┆           ┆           ┆   ┆           ┆ f64       ┆ list[f64] ┆ ]        │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 04 -      ┆ On SHN    ┆ 2024-Q2   ┆ 7741.85   ┆ … ┆ -0.28     ┆ -1.6      ┆ [35.98,   ┆ [17.58,  │
│ Oakland   ┆           ┆           ┆           ┆   ┆           ┆           ┆ 36.17, …  ┆ 18.26, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 34.56]    ┆ 17.15]   │
│ 04 -      ┆ Intersect ┆ 2024-Q2   ┆ 30717.35  ┆ … ┆ 0.7       ┆ 5.1       ┆ [31.82,   ┆ [13.47,  │
│ Oakland   ┆ s SHN     ┆           ┆           ┆   ┆           ┆           ┆ 33.84, …  ┆ 13.77, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 31.12]    ┆ 13.65]   │
│ 04 -      ┆ Other     ┆ 2024-Q2   ┆ 8169.32   ┆ … ┆ 0.47      ┆ 3.6       ┆ [40.08,   ┆ [13.23,  │
│ Oakland   ┆           ┆           ┆           ┆   ┆           ┆           ┆ 41.85, …  ┆ 13.46, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 38.0]     ┆ 13.06]   │
│ 04 -      ┆ On or Int ┆ 2024-Q2   ┆ 38459.2   ┆ … ┆ 0.49      ┆ 3.4       ┆ [32.57,   ┆ [14.2,   │
│ Oakland   ┆ ersects   ┆           ┆           ┆   ┆           ┆           ┆ 34.28, …  ┆ 14.6, …  │
│           ┆ SHN       ┆           ┆           ┆   ┆           ┆           ┆ 31.76]    ┆ 14.27]   │
│ 04 -      ┆ Total     ┆ 2024-Q2   ┆ 46628.52  ┆ … ┆ 0.51      ┆ 3.6       ┆ [33.75,   ┆ [14.04,  │
│ Oakland   ┆           ┆           ┆           ┆   ┆           ┆           ┆ 35.49, …  ┆ 14.41, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 32.7]     ┆ 14.08]   │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘, _body=<great_tables._gt_data.Body object at 0x7979517eca30>, _boxhead=Boxhead([ColInfo(var='caltrans_district', type=<ColInfoTypeEnum.hidden: 4>, column_label='caltrans_district', column_align='center', column_width=None), ColInfo(var='category', type=<ColInfoTypeEnum.default: 1>, column_label='Category', column_align='left', column_width=None), ColInfo(var='year_quarter', type=<ColInfoTypeEnum.hidden: 4>, column_label='year_quarter', column_align='center', column_width=None), ColInfo(var='service_hours', type=<ColInfoTypeEnum.hidden: 4>, column_label='service_hours', column_align='center', column_width=None), ColInfo(var='n_routes', type=<ColInfoTypeEnum.hidden: 4>, column_label='n_routes', column_align='center', column_width=None), ColInfo(var='n_dates', type=<ColInfoTypeEnum.hidden: 4>, column_label='n_dates', column_align='center', column_width=None), ColInfo(var='daily_service_hours', type=<ColInfoTypeEnum.default: 1>, column_label='Daily Service Hours', column_align='center', column_width=None), ColInfo(var='service_hours_per_route', type=<ColInfoTypeEnum.default: 1>, column_label='Service Hours per Route', column_align='center', column_width=None), ColInfo(var='daily_routes', type=<ColInfoTypeEnum.default: 1>, column_label='# Routes', column_align='center', column_width=None), ColInfo(var='change_service_hours_per_route', type=<ColInfoTypeEnum.default: 1>, column_label='Change from Prior', column_align='center', column_width=None), ColInfo(var='pct_change_service_hours_per_route', type=<ColInfoTypeEnum.hidden: 4>, column_label='% Change', column_align='center', column_width=None), ColInfo(var='service_hours_per_ro

GT(_tbl_data=shape: (5, 20)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ caltrans_ ┆ category  ┆ year_quar ┆ service_h ┆ … ┆ change_sp ┆ pct_chang ┆ service_h ┆ speed_mp │
│ district  ┆ ---       ┆ ter       ┆ ours      ┆   ┆ eed_mph   ┆ e_speed_m ┆ ours_per_ ┆ h_ts     │
│ ---       ┆ str       ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ph        ┆ route_ts  ┆ ---      │
│ str       ┆           ┆ str       ┆ f64       ┆   ┆ f64       ┆ ---       ┆ ---       ┆ list[f64 │
│           ┆           ┆           ┆           ┆   ┆           ┆ f64       ┆ list[f64] ┆ ]        │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 05 - San  ┆ On SHN    ┆ 2024-Q2   ┆ 2595.31   ┆ … ┆ 0.74      ┆ 3.0       ┆ [15.16,   ┆ [22.65,  │
│ Luis      ┆           ┆           ┆           ┆   ┆           ┆           ┆ 14.04, …  ┆ 22.78, … │
│ Obispo    ┆           ┆           ┆           ┆   ┆           ┆           ┆ 17.66]    ┆ 24.5]    │
│ 05 - San  ┆ Intersect ┆ 2024-Q2   ┆ 2874.54   ┆ … ┆ 0.57      ┆ 4.0       ┆ [13.68,   ┆ [13.73,  │
│ Luis      ┆ s SHN     ┆           ┆           ┆   ┆           ┆           ┆ 14.22, …  ┆ 13.66, … │
│ Obispo    ┆           ┆           ┆           ┆   ┆           ┆           ┆ 13.89]    ┆ 14.33]   │
│ 05 - San  ┆ Other     ┆ 2024-Q2   ┆ 451.43    ┆ … ┆ -0.84     ┆ -4.7      ┆ [11.24,   ┆ [16.14,  │
│ Luis      ┆           ┆           ┆           ┆   ┆           ┆           ┆ 12.25, …  ┆ 16.82, … │
│ Obispo    ┆           ┆           ┆           ┆   ┆           ┆           ┆ 14.11]    ┆ 17.75]   │
│ 05 - San  ┆ On or Int ┆ 2024-Q2   ┆ 5469.85   ┆ … ┆ 0.88      ┆ 4.8       ┆ [14.25,   ┆ [16.66,  │
│ Luis      ┆ ersects   ┆           ┆           ┆   ┆           ┆           ┆ 14.15, …  ┆ 16.69, … │
│ Obispo    ┆ SHN       ┆           ┆           ┆   ┆           ┆           ┆ 15.45]    ┆ 18.5]    │
│ 05 - San  ┆ Total     ┆ 2024-Q2   ┆ 5921.28   ┆ … ┆ 0.76      ┆ 4.1       ┆ [13.99,   ┆ [16.61,  │
│ Luis      ┆           ┆           ┆           ┆   ┆           ┆           ┆ 13.98, …  ┆ 16.7, …  │
│ Obispo    ┆           ┆           ┆           ┆   ┆           ┆           ┆ 15.34]    ┆ 18.44]   │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘, _body=<great_tables._gt_data.Body object at 0x7979517af460>, _boxhead=Boxhead([ColInfo(var='caltrans_district', type=<ColInfoTypeEnum.hidden: 4>, column_label='caltrans_district', column_align='center', column_width=None), ColInfo(var='category', type=<ColInfoTypeEnum.default: 1>, column_label='Category', column_align='left', column_width=None), ColInfo(var='year_quarter', type=<ColInfoTypeEnum.hidden: 4>, column_label='year_quarter', column_align='center', column_width=None), ColInfo(var='service_hours', type=<ColInfoTypeEnum.hidden: 4>, column_label='service_hours', column_align='center', column_width=None), ColInfo(var='n_routes', type=<ColInfoTypeEnum.hidden: 4>, column_label='n_routes', column_align='center', column_width=None), ColInfo(var='n_dates', type=<ColInfoTypeEnum.hidden: 4>, column_label='n_dates', column_align='center', column_width=None), ColInfo(var='daily_service_hours', type=<ColInfoTypeEnum.default: 1>, column_label='Daily Service Hours', column_align='center', column_width=None), ColInfo(var='service_hours_per_route', type=<ColInfoTypeEnum.default: 1>, column_label='Service Hours per Route', column_align='center', column_width=None), ColInfo(var='daily_routes', type=<ColInfoTypeEnum.default: 1>, column_label='# Routes', column_align='center', column_width=None), ColInfo(var='change_service_hours_per_route', type=<ColInfoTypeEnum.default: 1>, column_label='Change from Prior', column_align='center', column_width=None), ColInfo(var='pct_change_service_hours_per_route', type=<ColInfoTypeEnum.hidden: 4>, column_label='% Change', column_align='center', column_width=None), ColInfo(var='service_hours_per_ro

...

GT(_tbl_data=shape: (5, 20)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ caltrans_ ┆ category  ┆ year_quar ┆ service_h ┆ … ┆ change_sp ┆ pct_chang ┆ service_h ┆ speed_mp │
│ district  ┆ ---       ┆ ter       ┆ ours      ┆   ┆ eed_mph   ┆ e_speed_m ┆ ours_per_ ┆ h_ts     │
│ ---       ┆ str       ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ph        ┆ route_ts  ┆ ---      │
│ str       ┆           ┆ str       ┆ f64       ┆   ┆ f64       ┆ ---       ┆ ---       ┆ list[f64 │
│           ┆           ┆           ┆           ┆   ┆           ┆ f64       ┆ list[f64] ┆ ]        │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 08 - San  ┆ On SHN    ┆ 2024-Q2   ┆ 3580.33   ┆ … ┆ -0.19     ┆ -0.7      ┆ [19.11,   ┆ [28.58,  │
│ Bernardin ┆           ┆           ┆           ┆   ┆           ┆           ┆ 20.69, …  ┆ 27.44, … │
│ o         ┆           ┆           ┆           ┆   ┆           ┆           ┆ 21.44]    ┆ 25.62]   │
│ 08 - San  ┆ Intersect ┆ 2024-Q2   ┆ 5985.29   ┆ … ┆ 0.83      ┆ 4.9       ┆ [25.57,   ┆ [17.84,  │
│ Bernardin ┆ s SHN     ┆           ┆           ┆   ┆           ┆           ┆ 26.87, …  ┆ 17.6, …  │
│ o         ┆           ┆           ┆           ┆   ┆           ┆           ┆ 28.1]     ┆ 17.0]    │
│ 08 - San  ┆ Other     ┆ 2024-Q2   ┆ 4789.12   ┆ … ┆ 0.71      ┆ 3.6       ┆ [24.38,   ┆ [21.7,   │
│ Bernardin ┆           ┆           ┆           ┆   ┆           ┆           ┆ 24.44, …  ┆ 21.61, … │
│ o         ┆           ┆           ┆           ┆   ┆           ┆           ┆ 23.83]    ┆ 19.83]   │
│ 08 - San  ┆ On or Int ┆ 2024-Q2   ┆ 9565.62   ┆ … ┆ 0.85      ┆ 4.2       ┆ [23.11,   ┆ [21.16,  │
│ Bernardin ┆ ersects   ┆           ┆           ┆   ┆           ┆           ┆ 24.43, …  ┆ 20.68, … │
│ o         ┆ SHN       ┆           ┆           ┆   ┆           ┆           ┆ 25.17]    ┆ 20.07]   │
│ 08 - San  ┆ Total     ┆ 2024-Q2   ┆ 14354.74  ┆ … ┆ 0.81      ┆ 4.0       ┆ [23.53,   ┆ [21.31,  │
│ Bernardin ┆           ┆           ┆           ┆   ┆           ┆           ┆ 24.43, …  ┆ 20.93, … │
│ o         ┆           ┆           ┆           ┆   ┆           ┆           ┆ 24.71]    ┆ 20.0]    │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘, _body=<great_tables._gt_data.Body object at 0x7979517f9d30>, _boxhead=Boxhead([ColInfo(var='caltrans_district', type=<ColInfoTypeEnum.hidden: 4>, column_label='caltrans_district', column_align='center', column_width=None), ColInfo(var='category', type=<ColInfoTypeEnum.default: 1>, column_label='Category', column_align='left', column_width=None), ColInfo(var='year_quarter', type=<ColInfoTypeEnum.hidden: 4>, column_label='year_quarter', column_align='center', column_width=None), ColInfo(var='service_hours', type=<ColInfoTypeEnum.hidden: 4>, column_label='service_hours', column_align='center', column_width=None), ColInfo(var='n_routes', type=<ColInfoTypeEnum.hidden: 4>, column_label='n_routes', column_align='center', column_width=None), ColInfo(var='n_dates', type=<ColInfoTypeEnum.hidden: 4>, column_label='n_dates', column_align='center', column_width=None), ColInfo(var='daily_service_hours', type=<ColInfoTypeEnum.default: 1>, column_label='Daily Service Hours', column_align='center', column_width=None), ColInfo(var='service_hours_per_route', type=<ColInfoTypeEnum.default: 1>, column_label='Service Hours per Route', column_align='center', column_width=None), ColInfo(var='daily_routes', type=<ColInfoTypeEnum.default: 1>, column_label='# Routes', column_align='center', column_width=None), ColInfo(var='change_service_hours_per_route', type=<ColInfoTypeEnum.default: 1>, column_label='Change from Prior', column_align='center', column_width=None), ColInfo(var='pct_change_service_hours_per_route', type=<ColInfoTypeEnum.hidden: 4>, column_label='% Change', column_align='center', column_width=None), ColInfo(var='service_hours_per_ro

GT(_tbl_data=shape: (5, 20)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ caltrans_ ┆ category  ┆ year_quar ┆ service_h ┆ … ┆ change_sp ┆ pct_chang ┆ service_h ┆ speed_mp │
│ district  ┆ ---       ┆ ter       ┆ ours      ┆   ┆ eed_mph   ┆ e_speed_m ┆ ours_per_ ┆ h_ts     │
│ ---       ┆ str       ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ph        ┆ route_ts  ┆ ---      │
│ str       ┆           ┆ str       ┆ f64       ┆   ┆ f64       ┆ ---       ┆ ---       ┆ list[f64 │
│           ┆           ┆           ┆           ┆   ┆           ┆ f64       ┆ list[f64] ┆ ]        │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 09 -      ┆ On SHN    ┆ 2024-Q2   ┆ 214.91    ┆ … ┆ 1.7       ┆ 4.0       ┆ [9.5,     ┆ [null,   │
│ Bishop    ┆           ┆           ┆           ┆   ┆           ┆           ┆ 7.82, …   ┆ 41.49, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 9.34]     ┆ 42.42]   │
│ 09 -      ┆ Intersect ┆ 2024-Q2   ┆ 99.59     ┆ … ┆ 0.3       ┆ 2.5       ┆ [13.31,   ┆ [6.21,   │
│ Bishop    ┆ s SHN     ┆           ┆           ┆   ┆           ┆           ┆ 14.84, …  ┆ 11.97, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 9.96]     ┆ 11.82]   │
│ 09 -      ┆ Other     ┆ 2024-Q2   ┆ 7.5       ┆ … ┆ 2.2       ┆ 12.0      ┆ [18.48,   ┆ [16.12,  │
│ Bishop    ┆           ┆           ┆           ┆   ┆           ┆           ┆ 7.5]      ┆ 18.32]   │
│ 09 -      ┆ On or Int ┆ 2024-Q2   ┆ 314.5     ┆ … ┆ 2.69      ┆ 7.9       ┆ [11.23,   ┆ [6.21,   │
│ Bishop    ┆ ersects   ┆           ┆           ┆   ┆           ┆           ┆ 10.35, …  ┆ 24.62, … │
│           ┆ SHN       ┆           ┆           ┆   ┆           ┆           ┆ 9.53]     ┆ 34.07]   │
│ 09 -      ┆ Total     ┆ 2024-Q2   ┆ 322.0     ┆ … ┆ 2.01      ┆ 6.0       ┆ [11.23,   ┆ [6.21,   │
│ Bishop    ┆           ┆           ┆           ┆   ┆           ┆           ┆ 10.35, …  ┆ 24.62, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 9.47]     ┆ 33.39]   │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘, _body=<great_tables._gt_data.Body object at 0x797951482d30>, _boxhead=Boxhead([ColInfo(var='caltrans_district', type=<ColInfoTypeEnum.hidden: 4>, column_label='caltrans_district', column_align='center', column_width=None), ColInfo(var='category', type=<ColInfoTypeEnum.default: 1>, column_label='Category', column_align='left', column_width=None), ColInfo(var='year_quarter', type=<ColInfoTypeEnum.hidden: 4>, column_label='year_quarter', column_align='center', column_width=None), ColInfo(var='service_hours', type=<ColInfoTypeEnum.hidden: 4>, column_label='service_hours', column_align='center', column_width=None), ColInfo(var='n_routes', type=<ColInfoTypeEnum.hidden: 4>, column_label='n_routes', column_align='center', column_width=None), ColInfo(var='n_dates', type=<ColInfoTypeEnum.hidden: 4>, column_label='n_dates', column_align='center', column_width=None), ColInfo(var='daily_service_hours', type=<ColInfoTypeEnum.default: 1>, column_label='Daily Service Hours', column_align='center', column_width=None), ColInfo(var='service_hours_per_route', type=<ColInfoTypeEnum.default: 1>, column_label='Service Hours per Route', column_align='center', column_width=None), ColInfo(var='daily_routes', type=<ColInfoTypeEnum.default: 1>, column_label='# Routes', column_align='center', column_width=None), ColInfo(var='change_service_hours_per_route', type=<ColInfoTypeEnum.default: 1>, column_label='Change from Prior', column_align='center', column_width=None), ColInfo(var='pct_change_service_hours_per_route', type=<ColInfoTypeEnum.hidden: 4>, column_label='% Change', column_align='center', column_width=None), ColInfo(var='service_hours_per_route_ts', type=<ColInfoTypeEnum.default: 1>, column_label='Time-series', column_align='center', column

GT(_tbl_data=shape: (5, 20)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ caltrans_ ┆ category  ┆ year_quar ┆ service_h ┆ … ┆ change_sp ┆ pct_chang ┆ service_h ┆ speed_mp │
│ district  ┆ ---       ┆ ter       ┆ ours      ┆   ┆ eed_mph   ┆ e_speed_m ┆ ours_per_ ┆ h_ts     │
│ ---       ┆ str       ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ph        ┆ route_ts  ┆ ---      │
│ str       ┆           ┆ str       ┆ f64       ┆   ┆ f64       ┆ ---       ┆ ---       ┆ list[f64 │
│           ┆           ┆           ┆           ┆   ┆           ┆ f64       ┆ list[f64] ┆ ]        │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 10 -      ┆ On SHN    ┆ 2024-Q2   ┆ 1712.85   ┆ … ┆ 0.26      ┆ 0.9       ┆ [15.29,   ┆ [29.68,  │
│ Stockton  ┆           ┆           ┆           ┆   ┆           ┆           ┆ 15.3, …   ┆ 28.55, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 15.86]    ┆ 27.91]   │
│ 10 -      ┆ Intersect ┆ 2024-Q2   ┆ 3031.91   ┆ … ┆ 0.24      ┆ 1.7       ┆ [16.07,   ┆ [16.02,  │
│ Stockton  ┆ s SHN     ┆           ┆           ┆   ┆           ┆           ┆ 16.37, …  ┆ 15.09, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 15.63]    ┆ 14.1]    │
│ 10 -      ┆ Other     ┆ 2024-Q2   ┆ 2146.57   ┆ … ┆ 0.91      ┆ 5.5       ┆ [16.67,   ┆ [14.0,   │
│ Stockton  ┆           ┆           ┆           ┆   ┆           ┆           ┆ 17.09, …  ┆ 14.14, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 20.64]    ┆ 16.53]   │
│ 10 -      ┆ On or Int ┆ 2024-Q2   ┆ 4744.76   ┆ … ┆ 0.28      ┆ 1.5       ┆ [15.8,    ┆ [20.27,  │
│ Stockton  ┆ ersects   ┆           ┆           ┆   ┆           ┆           ┆ 15.98, …  ┆ 19.5, …  │
│           ┆ SHN       ┆           ┆           ┆   ┆           ┆           ┆ 15.71]    ┆ 18.64]   │
│ 10 -      ┆ Total     ┆ 2024-Q2   ┆ 6891.33   ┆ … ┆ 0.42      ┆ 2.3       ┆ [15.96,   ┆ [19.17,  │
│ Stockton  ┆           ┆           ┆           ┆   ┆           ┆           ┆ 16.18, …  ┆ 18.56, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 16.97]    ┆ 18.05]   │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘, _body=<great_tables._gt_data.Body object at 0x7979517dd820>, _boxhead=Boxhead([ColInfo(var='caltrans_district', type=<ColInfoTypeEnum.hidden: 4>, column_label='caltrans_district', column_align='center', column_width=None), ColInfo(var='category', type=<ColInfoTypeEnum.default: 1>, column_label='Category', column_align='left', column_width=None), ColInfo(var='year_quarter', type=<ColInfoTypeEnum.hidden: 4>, column_label='year_quarter', column_align='center', column_width=None), ColInfo(var='service_hours', type=<ColInfoTypeEnum.hidden: 4>, column_label='service_hours', column_align='center', column_width=None), ColInfo(var='n_routes', type=<ColInfoTypeEnum.hidden: 4>, column_label='n_routes', column_align='center', column_width=None), ColInfo(var='n_dates', type=<ColInfoTypeEnum.hidden: 4>, column_label='n_dates', column_align='center', column_width=None), ColInfo(var='daily_service_hours', type=<ColInfoTypeEnum.default: 1>, column_label='Daily Service Hours', column_align='center', column_width=None), ColInfo(var='service_hours_per_route', type=<ColInfoTypeEnum.default: 1>, column_label='Service Hours per Route', column_align='center', column_width=None), ColInfo(var='daily_routes', type=<ColInfoTypeEnum.default: 1>, column_label='# Routes', column_align='center', column_width=None), ColInfo(var='change_service_hours_per_route', type=<ColInfoTypeEnum.default: 1>, column_label='Change from Prior', column_align='center', column_width=None), ColInfo(var='pct_change_service_hours_per_route', type=<ColInfoTypeEnum.hidden: 4>, column_label='% Change', column_align='center', column_width=None), ColInfo(var='service_hours_per_ro

GT(_tbl_data=shape: (5, 20)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ caltrans_ ┆ category  ┆ year_quar ┆ service_h ┆ … ┆ change_sp ┆ pct_chang ┆ service_h ┆ speed_mp │
│ district  ┆ ---       ┆ ter       ┆ ours      ┆   ┆ eed_mph   ┆ e_speed_m ┆ ours_per_ ┆ h_ts     │
│ ---       ┆ str       ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ph        ┆ route_ts  ┆ ---      │
│ str       ┆           ┆ str       ┆ f64       ┆   ┆ f64       ┆ ---       ┆ ---       ┆ list[f64 │
│           ┆           ┆           ┆           ┆   ┆           ┆ f64       ┆ list[f64] ┆ ]        │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 11 - San  ┆ On SHN    ┆ 2024-Q2   ┆ 2128.85   ┆ … ┆ 0.82      ┆ 3.6       ┆ [24.45,   ┆ [21.99,  │
│ Diego     ┆           ┆           ┆           ┆   ┆           ┆           ┆ 24.71, …  ┆ 23.46, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 28.38]    ┆ 22.83]   │
│ 11 - San  ┆ Intersect ┆ 2024-Q2   ┆ 14664.81  ┆ … ┆ 0.72      ┆ 5.1       ┆ [41.74,   ┆ [14.06,  │
│ Diego     ┆ s SHN     ┆           ┆           ┆   ┆           ┆           ┆ 41.66, …  ┆ 14.39, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 42.88]    ┆ 14.08]   │
│ 11 - San  ┆ Other     ┆ 2024-Q2   ┆ 2700.69   ┆ … ┆ 0.62      ┆ 3.9       ┆ [27.88,   ┆ [16.14,  │
│ Diego     ┆           ┆           ┆           ┆   ┆           ┆           ┆ 28.37, …  ┆ 15.78, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 33.34]    ┆ 15.8]    │
│ 11 - San  ┆ On or Int ┆ 2024-Q2   ┆ 16793.66  ┆ … ┆ 0.77      ┆ 5.1       ┆ [38.66,   ┆ [15.03,  │
│ Diego     ┆ ersects   ┆           ┆           ┆   ┆           ┆           ┆ 38.63, …  ┆ 15.55, … │
│           ┆ SHN       ┆           ┆           ┆   ┆           ┆           ┆ 40.27]    ┆ 15.21]   │
│ 11 - San  ┆ Total     ┆ 2024-Q2   ┆ 19494.35  ┆ … ┆ 0.75      ┆ 4.9       ┆ [36.97,   ┆ [15.17,  │
│ Diego     ┆           ┆           ┆           ┆   ┆           ┆           ┆ 37.03, …  ┆ 15.58, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 39.15]    ┆ 15.3]    │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘, _body=<great_tables._gt_data.Body object at 0x79795144ee80>, _boxhead=Boxhead([ColInfo(var='caltrans_district', type=<ColInfoTypeEnum.hidden: 4>, column_label='caltrans_district', column_align='center', column_width=None), ColInfo(var='category', type=<ColInfoTypeEnum.default: 1>, column_label='Category', column_align='left', column_width=None), ColInfo(var='year_quarter', type=<ColInfoTypeEnum.hidden: 4>, column_label='year_quarter', column_align='center', column_width=None), ColInfo(var='service_hours', type=<ColInfoTypeEnum.hidden: 4>, column_label='service_hours', column_align='center', column_width=None), ColInfo(var='n_routes', type=<ColInfoTypeEnum.hidden: 4>, column_label='n_routes', column_align='center', column_width=None), ColInfo(var='n_dates', type=<ColInfoTypeEnum.hidden: 4>, column_label='n_dates', column_align='center', column_width=None), ColInfo(var='daily_service_hours', type=<ColInfoTypeEnum.default: 1>, column_label='Daily Service Hours', column_align='center', column_width=None), ColInfo(var='service_hours_per_route', type=<ColInfoTypeEnum.default: 1>, column_label='Service Hours per Route', column_align='center', column_width=None), ColInfo(var='daily_routes', type=<ColInfoTypeEnum.default: 1>, column_label='# Routes', column_align='center', column_width=None), ColInfo(var='change_service_hours_per_route', type=<ColInfoTypeEnum.default: 1>, column_label='Change from Prior', column_align='center', column_width=None), ColInfo(var='pct_change_service_hours_per_route', type=<ColInfoTypeEnum.hidden: 4>, column_label='% Change', column_align='center', column_width=None), ColInfo(var='service_hours_per_ro

GT(_tbl_data=shape: (5, 20)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ caltrans_ ┆ category  ┆ year_quar ┆ service_h ┆ … ┆ change_sp ┆ pct_chang ┆ service_h ┆ speed_mp │
│ district  ┆ ---       ┆ ter       ┆ ours      ┆   ┆ eed_mph   ┆ e_speed_m ┆ ours_per_ ┆ h_ts     │
│ ---       ┆ str       ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ph        ┆ route_ts  ┆ ---      │
│ str       ┆           ┆ str       ┆ f64       ┆   ┆ f64       ┆ ---       ┆ ---       ┆ list[f64 │
│           ┆           ┆           ┆           ┆   ┆           ┆ f64       ┆ list[f64] ┆ ]        │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 12 -      ┆ On SHN    ┆ 2024-Q2   ┆ 1321.65   ┆ … ┆ 0.27      ┆ 1.7       ┆ [53.13,   ┆ [16.42,  │
│ Irvine    ┆           ┆           ┆           ┆   ┆           ┆           ┆ 60.71, …  ┆ 16.56, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 47.2]     ┆ 16.05]   │
│ 12 -      ┆ Intersect ┆ 2024-Q2   ┆ 6618.05   ┆ … ┆ 0.53      ┆ 3.7       ┆ [114.9,   ┆ [14.5,   │
│ Irvine    ┆ s SHN     ┆           ┆           ┆   ┆           ┆           ┆ 99.34, …  ┆ 14.43, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 66.85]    ┆ 14.26]   │
│ 12 -      ┆ Other     ┆ 2024-Q2   ┆ 6530.87   ┆ … ┆ 0.61      ┆ 4.3       ┆ [70.19,   ┆ [14.97,  │
│ Irvine    ┆           ┆           ┆           ┆   ┆           ┆           ┆ 72.19, …  ┆ 14.4, …  │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 64.66]    ┆ 14.1]    │
│ 12 -      ┆ On or Int ┆ 2024-Q2   ┆ 7939.7    ┆ … ┆ 0.5       ┆ 3.4       ┆ [103.81,  ┆ [14.86,  │
│ Irvine    ┆ ersects   ┆           ┆           ┆   ┆           ┆           ┆ 92.65, …  ┆ 14.78, … │
│           ┆ SHN       ┆           ┆           ┆   ┆           ┆           ┆ 62.52]    ┆ 14.6]    │
│ 12 -      ┆ Total     ┆ 2024-Q2   ┆ 14470.57  ┆ … ┆ 0.56      ┆ 3.9       ┆ [89.19,   ┆ [14.92,  │
│ Irvine    ┆           ┆           ┆           ┆   ┆           ┆           ┆ 83.34, …  ┆ 14.59, … │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 63.47]    ┆ 14.34]   │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘, _body=<great_tables._gt_data.Body object at 0x797991cf0370>, _boxhead=Boxhead([ColInfo(var='caltrans_district', type=<ColInfoTypeEnum.hidden: 4>, column_label='caltrans_district', column_align='center', column_width=None), ColInfo(var='category', type=<ColInfoTypeEnum.default: 1>, column_label='Category', column_align='left', column_width=None), ColInfo(var='year_quarter', type=<ColInfoTypeEnum.hidden: 4>, column_label='year_quarter', column_align='center', column_width=None), ColInfo(var='service_hours', type=<ColInfoTypeEnum.hidden: 4>, column_label='service_hours', column_align='center', column_width=None), ColInfo(var='n_routes', type=<ColInfoTypeEnum.hidden: 4>, column_label='n_routes', column_align='center', column_width=None), ColInfo(var='n_dates', type=<ColInfoTypeEnum.hidden: 4>, column_label='n_dates', column_align='center', column_width=None), ColInfo(var='daily_service_hours', type=<ColInfoTypeEnum.default: 1>, column_label='Daily Service Hours', column_align='center', column_width=None), ColInfo(var='service_hours_per_route', type=<ColInfoTypeEnum.default: 1>, column_label='Service Hours per Route', column_align='center', column_width=None), ColInfo(var='daily_routes', type=<ColInfoTypeEnum.default: 1>, column_label='# Routes', column_align='center', column_width=None), ColInfo(var='change_service_hours_per_route', type=<ColInfoTypeEnum.default: 1>, column_label='Change from Prior', column_align='center', column_width=None), ColInfo(var='pct_change_service_hours_per_route', type=<ColInfoTypeEnum.hidden: 4>, column_label='% Change', column_align='center', column_width=None), ColInfo(var='service_hours_per_ro

## Operator Breakdown 

Only the SHN subtotal (on SHN and parallel) is shown for each operator.

In [8]:
def operator_table_specs(table, one_quarter):
    table2 = (
        table
          .cols_hide(["category"])
          .tab_style(
            style=style.text(
                weight="normal", style="normal", color=get_hex("black")),
            locations=loc.body(
                rows=pl.col("category") == "On or Intersects SHN"),
        ).cols_label(
            organization_name="Organization Name",
            name="Transit Operator",
            caltrans_district="District",
        ).tab_header(
            title = f"Service Hours and Speed by Operator  {one_quarter}",
            subtitle = f"Only On or Intersects SHN Shown"
          )
    )         
    
    return table2

table = plot_table(
    operator_df[
        operator_df.category=="On or Intersects SHN"
    ].sort_values(
        ["change_service_hours_per_route", "caltrans_district", "name"], 
        ascending=[False, True, True]
    ).reset_index(drop=True)
)

table = operator_table_specs(table, current_quarter)
display(table)

GT(_tbl_data=shape: (168, 22)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ name      ┆ organizat ┆ caltrans_ ┆ category  ┆ … ┆ change_sp ┆ pct_chang ┆ service_h ┆ speed_mp │
│ ---       ┆ ion_name  ┆ district  ┆ ---       ┆   ┆ eed_mph   ┆ e_speed_m ┆ ours_per_ ┆ h_ts     │
│ str       ┆ ---       ┆ ---       ┆ str       ┆   ┆ ---       ┆ ph        ┆ route_ts  ┆ ---      │
│           ┆ str       ┆ str       ┆           ┆   ┆ f64       ┆ ---       ┆ ---       ┆ list[f64 │
│           ┆           ┆           ┆           ┆   ┆           ┆ f64       ┆ list[f64] ┆ ]        │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ County    ┆ San       ┆ 05 - San  ┆ On or Int ┆ … ┆ null      ┆ null      ┆ [15.15,   ┆ [null,   │
│ Express   ┆ Benito    ┆ Luis      ┆ ersects   ┆   ┆           ┆           ┆ 15.92, …  ┆ null, …  │
│ Schedule  ┆ County    ┆ Obispo    ┆ SHN       ┆   ┆           ┆           ┆ 22.11]    ┆ null]    │
│           ┆ Local     ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆ Transp…   ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ LAX       ┆ Los       ┆ 07 - Los  ┆ On or Int ┆ … ┆ null      ┆ null      ┆ [40.81,   ┆ [null,   │
│ FlyAway   ┆ Angeles   ┆ Angeles   ┆ ersects   ┆   ┆           ┆           ┆ 40.81, …  ┆ null, …  │
│ Schedule  ┆ World     ┆           ┆ SHN       ┆   ┆           ┆           ┆ 67.95]    ┆ null]    │
│           ┆ Airports  ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ Bay Area  ┆ Alameda-C ┆ 04 -      ┆ On or Int ┆ … ┆ 0.13      ┆ 1.0       ┆ [32.15,   ┆ [13.51,  │
│ 511 AC    ┆ ontra     ┆ Oakland   ┆ ersects   ┆   ┆           ┆           ┆ 40.78, …  ┆ 13.38, … │
│ Transit   ┆ Costa     ┆           ┆ SHN       ┆   ┆           ┆           ┆ 37.59]    ┆ 13.19]   │
│ Schedu…   ┆ Transit   ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆ D…        ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ San Diego ┆ San Diego ┆ 11 - San  ┆ On or Int ┆ … ┆ -0.13     ┆ -0.9      ┆ [49.49,   ┆ [14.37,  │
│ Schedule  ┆ Metropoli ┆ Diego     ┆ ersects   ┆   ┆           ┆           ┆ 54.49]    ┆ 14.24]   │
│           ┆ tan       ┆           ┆ SHN       ┆   ┆           ┆           ┆           ┆          │
│           ┆ Transit…  ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ LA Metro  ┆ Los       ┆ 07 - Los  ┆ On or Int ┆ … ┆ 1.59      ┆ 6.4       ┆ [114.44,  ┆ [25.35,  │
│ Rail      ┆ Angeles   ┆ Angeles   ┆ ersects   ┆   ┆           ┆           ┆ 159.16, … ┆ 25.29, … │
│ Schedule  ┆ County    ┆           ┆ SHN       ┆   ┆           ┆           ┆ 194.1]    ┆ 24.98]   │
│           ┆ Metropoli ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆ ta…       ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ …         ┆ …         ┆ …         ┆ …         ┆ … ┆ …         ┆ …         ┆ …         ┆ …        │
│ Anaheim   ┆ Anaheim   ┆ 12 -      ┆ On or Int ┆ … ┆ null      ┆ null      ┆ [239.65,  ┆ [null,   │
│ Resort    ┆ Transport ┆ Irvine    ┆ ersects   ┆   ┆           ┆           ┆ 245.28, … ┆ null, …  │
│ Schedule  ┆ ation     ┆           ┆ SHN       ┆   ┆           ┆           ┆ 84.82]    ┆ null]    │
│           ┆ Network   ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ Redwood   ┆ Redwood   ┆ 01 -      ┆ On or Int ┆ … ┆ null      ┆ null      ┆ [3.59]    ┆ [21.18]  │
│ Coast     ┆ Coast     ┆ Eureka    ┆ ersects   ┆   ┆           ┆           ┆           ┆          │
│ Schedulel ┆ Transit   ┆           ┆ SHN       ┆   ┆           ┆           ┆           ┆          │
│           ┆ Authorit… ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ Roseville ┆ City of   ┆ 03 - 